<a href="https://colab.research.google.com/github/aritanaoya/football_analysis/blob/main/J1Predict_by_AutoML.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install pycaret==2.3.1
!pip install pyyaml==5.4.1
!pip install markupsafe==2.0.1

In [1]:
from pycaret.utils import enable_colab

enable_colab()

Colab mode enabled.


In [2]:
import numpy as np
import pandas as pd
import time

csv = '/content/seasonData_2021.csv'
data = pd.read_csv(csv)
data = data.drop(data.columns[[0,7,18]], axis=1)
data.shape

(380, 24)

In [3]:
data.to_csv("seasonData2021.csv",encoding = 'utf-8-sig')



# データの前処理

In [4]:
data['CBP_x'] = data['CBP_x'].str.replace('%', '').astype(np.float64) /100
data['shot acc_x'] = data['shot acc_x'].str.replace('%', '').astype(np.float64) / 100
data['possession_x'] = data['possession_x'].str.replace('%', '').astype(np.float64) / 100
data['CBP_y'] = data['CBP_y'].str.replace('%', '').astype(np.float64) / 100
data['shot acc_y'] = data['shot acc_y'].str.replace('%', '').astype(np.float64) / 100
data['possession_y'] = data['possession_y'].str.replace('%', '').astype(np.float64) / 100

## pandas profiling

In [5]:
#!pip install --upgrade pandas-profiling

In [6]:
# import pandas_profiling as pdp
# pdp.ProfileReport(data).to_file(output_file = 'profileReport.html')

## SetUP

In [8]:
import jinja2
from pycaret.regression import setup
data = data.drop('節', axis=1)
data = data.drop('開催日', axis=1)
def x(a,b):
    return a - b
data['homeScore']  = data.apply(lambda f: x(f['homeScore'],f['awayScore']), axis=1)
data = data.drop('awayScore', axis=1)
data = data.rename(columns={'homeScore': 'Score'})
data

/usr/local/lib/python3.7/dist-packages/distributed/config.py:20: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  defaults = yaml.load(f)


Team awayTeam  Score  KAGI_x  CBP_x  shot_x  shot acc_x  possession_x  \
0      広島       仙台      0      59  0.176      19       0.053         0.576   
1      神戸      Ｇ大阪      1      51  0.063       8       0.125         0.582   
2      大分       徳島      0      49  0.094      10       0.100         0.374   
3      福岡      名古屋     -1      41  0.033       4       0.000         0.505   
4     川崎Ｆ     横浜FM      2      44  0.137      18       0.111         0.469   
5     Ｃ大阪        柏      2      56  0.169      20       0.100         0.552   
6      鹿島       清水     -2      70  0.173      23       0.043         0.560   
7      湘南       鳥栖     -1      53  0.070       9       0.000         0.460   
8      札幌     横浜FC      4      66  0.209      23       0.217         0.543   
9      浦和     FC東京      0      47  0.086      11       0.091         0.587   
10     鳥栖       浦和      2      55  0.132      14       0.143         0.521   
11   横浜FC       大分     -1      54  0.175      21       0.048         0.509   
12    名古屋       札幌      1      49  0.092      11       0.091         0.457   
13     仙台      川崎Ｆ     -4      43  0.092      13       0.077         0.403   
14   横浜FM       広島      0      52  0.107      14       0.214         0.654   
15     徳島       神戸      0      59  0.093      11       0.091         0.402   
16     清水       福岡      0      51  0.072       8       0.250         0.471   
17    Ｇ大阪       鹿島     -1      31  0.078       8       0.000         0.479   
18   FC東京      Ｃ大阪      1      51  0.168      22       0.136         0.481   
19      柏       湘南      1      47  0.063       8       0.250         0.497   
20     浦和     横浜FC      2      49  0.090       9       0.222         0.519   
21     鳥栖       仙台      5      50  0.175      18       0.278         0.554   
22     福岡     横浜FM     -2      37  0.104      14       0.071         0.370   
23     鹿島       湘南      2      73  0.142      20       0.150         0.603   
24    Ｃ大阪       清水      1      56  0.104      11       0.182         0.490   
25      柏      名古屋     -1      54  0.068      10       0.000         0.503   
26    Ｇ大阪       大分      1      74  0.186      18       0.111         0.524   
27   FC東京       神戸     -1      62  0.135      18       0.111         0.398   
28    川崎Ｆ       徳島      2      71  0.162      18       0.111         0.492   
29     広島       札幌      1      47  0.112      13       0.154         0.398   
30    川崎Ｆ        柏      1      55  0.102      14       0.071         0.578   
31     札幌      Ｇ大阪     -2      53  0.124      16       0.000         0.576   
32     湘南       仙台      2      47  0.092      11       0.273         0.418   
33     清水       鳥栖      0      59  0.049       4       0.000         0.339   
34   横浜FC      Ｃ大阪     -3      39  0.087      11       0.091         0.491   
35     大分     FC東京      0      45  0.095      10       0.100         0.558   
36     神戸      名古屋     -1      70  0.093      10       0.000         0.638   
37   横浜FM       浦和      3      65  0.179      21       0.143         0.463   
38     鹿島       広島      0      55  0.171      24       0.042         0.593   
39     徳島       福岡     -1      51  0.099      11       0.091         0.612   
40     浦和       札幌      0      44  0.105      11       0.000         0.415   
41     広島       清水      1      69  0.109      11       0.091         0.528   
42    名古屋     横浜FC      3      52  0.118      12       0.250         0.553   
43   横浜FM       徳島      1      51  0.063       9       0.111         0.537   
44     神戸      川崎Ｆ      0      44  0.062       9       0.111         0.495   
45     仙台      Ｇ大阪     -1      55  0.152      16       0.000         0.561   
46   FC東京       湘南      1      43  0.132      15       0.200         0.470   
47    Ｃ大阪       大分      1      71  0.053       6       0.167         0.507   
48     鳥栖        柏      2      41  0.068       8       0.250         0.534   
49     福岡       鹿島      1      39  0.050       6       0.167         0.510   
50      柏       清水     -1  

In [9]:
setup = setup(data, target="Score",
        session_id = 123)

Description             Value
0                               session_id               123
1                                   Target             Score
2                            Original Data         (380, 21)
3                           Missing Values             False
4                         Numeric Features                18
5                     Categorical Features                 2
6                         Ordinal Features             False
7                High Cardinality Features             False
8                  High Cardinality Method              None
9                    Transformed Train Set         (265, 56)
10                    Transformed Test Set         (115, 56)
11                      Shuffle Train-Test              True
12                     Stratify Train-Test             False
13                          Fold Generator             KFold
14                             Fold Number                10
15                                CPU Jobs                -1
16                                 Use GPU             False
17                          Log Experiment             False
18                         Experiment Name  reg-default-name
19                                     USI              c6a4
20                         Imputation Type            simple
21          Iterative Imputation Iteration              None
22                         Numeric Imputer              mean
23      Iterative Imputation Numeric Model              None
24                     Categorical Imputer          constant
25  Iterative Imputation Categorical Model              None
26           Unknown Categoricals Handling    least_frequent
27                               Normalize             False
28                        Normalize Method              None
29                          Transformation             False
30                   Transformation Method              None
31                                     PCA             False
32                              PCA Method              None
33                          PCA Components              None
34                     Ignore Low Variance             False
35                     Combine Rare Levels             False
36                    Rare Level Threshold              None
37                         Numeric Binning             False
38                         Remove Outliers             False
39                      Outliers Threshold              None
40                Remove Multicollinearity             False
41             Multicollinearity Threshold              None
42                              Clustering             False
43                    Clustering Iteration              None
44                     Polynomial Features             False
45                       Polynomial Degree              None
46                    Trignometry Features             False
47                    Polynomial Threshold              None
48                          Group Features             False
49                       Feature Selection             False
50                Feature Selection Method           classic
51            Features Selection Threshold              None
52                     Feature Interaction             False
53                           Feature Ratio             False
54                   Interaction Threshold              None
55                        Transform Target             False
56                 Transform Target Method           box-cox

In [10]:
setup

({'mae': <pycaret.containers.metrics.regression.MAEMetricContainer at 0x7fe2662db050>,
  'mape': <pycaret.containers.metrics.regression.MAPEMetricContainer at 0x7fe266162610>,
  'mse': <pycaret.containers.metrics.regression.MSEMetricContainer at 0x7fe2662db090>,
  'r2': <pycaret.containers.metrics.regression.R2MetricContainer at 0x7fe2662db550>,
  'rmse': <pycaret.containers.metrics.regression.RMSEMetricContainer at 0x7fe2662db190>,
  'rmsle': <pycaret.containers.metrics.regression.RMSLEMetricContainer at 0x7fe266162090>},
 0       0
 1       1
 2       0
 3      -1
 4       2
        ..
 375     1
 376     0
 377     0
 378    -1
 379    -2
 Name: Score, Length: 380, dtype: object,
 Pipeline(memory=None,
          steps=[('dtypes',
                  DataTypes_Auto_infer(categorical_features=[],
                                       display_types=True, features_todrop=[],
                                       id_columns=[], ml_usecase='regression',
                                   

# 適用モデルの選定

In [11]:
from pycaret.regression import compare_models

best_model = compare_models()  # 全てのモデルを訓練し、評価する

Model           MAE           MSE  \
gbr           Gradient Boosting Regressor  4.285000e-01  4.302000e-01   
et                  Extra Trees Regressor  4.608000e-01  5.549000e-01   
rf                Random Forest Regressor  4.846000e-01  5.969000e-01   
omp           Orthogonal Matching Pursuit  5.341000e-01  6.321000e-01   
lr                      Linear Regression  6.187000e-01  6.923000e-01   
br                         Bayesian Ridge  6.305000e-01  6.948000e-01   
ada                    AdaBoost Regressor  6.488000e-01  8.306000e-01   
ridge                    Ridge Regression  6.954000e-01  8.128000e-01   
dt                Decision Tree Regressor  6.567000e-01  1.147000e+00   
huber                     Huber Regressor  1.046400e+00  1.829500e+00   
en                            Elastic Net  1.174900e+00  2.539900e+00   
lasso                    Lasso Regression  1.266000e+00  2.868800e+00   
lightgbm  Light Gradient Boosting Machine  0.000000e+00  0.000000e+00   
llar         Lasso Least Angle Regression  1.377400e+00  3.296000e+00   
par          Passive Aggressive Regressor  1.901800e+00  5.932200e+00   
lar                Least Angle Regression  2.262899e+06  1.357916e+14   

                  RMSE            R2  RMSLE          MAPE  TT (Sec)  
gbr       6.353000e-01  8.604000e-01    0.0  2.772000e-01     0.112  
et        7.318000e-01  8.159000e-01    0.0  2.880000e-01     0.454  
rf        7.443000e-01  8.122000e-01    0.0  3.004000e-01     0.505  
omp       7.704000e-01  7.885000e-01    0.0  3.541000e-01     0.014  
lr        8.148000e-01  7.664000e-01    0.0  4.097000e-01     0.299  
br        8.204000e-01  7.649000e-01    0.0  4.152000e-01     0.015  
ada       8.910000e-01  7.343000e-01    0.0  4.101000e-01     0.102  
ridge     8.916000e-01  7.225000e-01    0.0  4.477000e-01     0.013  
dt        1.058300e+00  5.999000e-01    0.0  4.296000e-01     0.280  
huber     1.340700e+00  3.723000e-01    0.0  6.515000e-01     0.042  
en        1.576900e+00  1.638000e-01    0.0  7.766000e-01     0.013  
lasso     1.675300e+00  6.940000e-02    0.0  8.502000e-01     0.013  
lightgbm  0.000000e+00  0.000000e+00    0.0  0.000000e+00     0.012  
llar      1.794500e+00 -5.890000e-02    0.0  9.742000e-01     0.013  
par       2.271000e+00 -9.847000e-01    0.0  1.292500e+00     0.015  
lar       3.691683e+06 -6.670618e+13    0.0  1.765034e+06     0.024

In [12]:
print(best_model)

GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                          init=None, learning_rate=0.1, loss='ls', max_depth=3,
                          max_features=None, max_leaf_nodes=None,
                          min_impurity_decrease=0.0, min_impurity_split=None,
                          min_samples_leaf=1, min_samples_split=2,
                          min_weight_fraction_leaf=0.0, n_estimators=100,
                          n_iter_no_change=None, presort='deprecated',
                          random_state=123, subsample=1.0, tol=0.0001,
                          validation_fraction=0.1, verbose=0, warm_start=False)


## Create Model

In [14]:
# from pycaret.regression import models

# models()  # 機械学習モデルの一覧

In [15]:
from pycaret.regression import create_model

gbr = create_model("gbr")  # GradientBoostingRegressorのモデルを作成

MAE     MSE    RMSE      R2  RMSLE    MAPE
0     0.2814  0.1995  0.4467  0.9020   -0.0  0.2295
1     0.4129  0.3443  0.5868  0.8405   -0.0  0.2904
2     0.4793  0.5098  0.7140  0.8409   -0.0  0.2647
3     0.3280  0.1848  0.4299  0.9391   -0.0  0.2442
4     0.6253  0.9522  0.9758  0.7796   -0.0  0.2781
5     0.3869  0.2960  0.5440  0.8969   -0.0  0.2898
6     0.3488  0.2793  0.5285  0.8670   -0.0  0.2566
7     0.4983  0.6137  0.7834  0.7513   -0.0  0.3380
8     0.5128  0.5947  0.7711  0.8520   -0.0  0.3548
9     0.4110  0.3280  0.5727  0.9349   -0.0  0.2256
Mean  0.4285  0.4302  0.6353  0.8604    0.0  0.2772
SD    0.0968  0.2262  0.1632  0.0584    0.0  0.0408

In [16]:
print(gbr)

GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                          init=None, learning_rate=0.1, loss='ls', max_depth=3,
                          max_features=None, max_leaf_nodes=None,
                          min_impurity_decrease=0.0, min_impurity_split=None,
                          min_samples_leaf=1, min_samples_split=2,
                          min_weight_fraction_leaf=0.0, n_estimators=100,
                          n_iter_no_change=None, presort='deprecated',
                          random_state=123, subsample=1.0, tol=0.0001,
                          validation_fraction=0.1, verbose=0, warm_start=False)


# モデルのチューニング

In [17]:
from pycaret.regression import tune_model

tuned_gbr = tune_model(gbr)  # ハイパーパラメータの調整

MAE     MSE    RMSE      R2  RMSLE    MAPE
0     0.3318  0.2417  0.4917  0.8812   -0.0  0.2892
1     0.4102  0.3552  0.5960  0.8355   -0.0  0.3398
2     0.4587  0.3765  0.6136  0.8825   -0.0  0.2636
3     0.3825  0.2093  0.4575  0.9311   -0.0  0.2730
4     0.4494  0.5554  0.7453  0.8715   -0.0  0.1819
5     0.4022  0.2992  0.5470  0.8958   -0.0  0.3218
6     0.3876  0.3933  0.6271  0.8128   -0.0  0.2456
7     0.4576  0.4961  0.7043  0.7990   -0.0  0.2971
8     0.5829  0.7970  0.8928  0.8016   -0.0  0.4245
9     0.4885  0.4128  0.6425  0.9180   -0.0  0.2988
Mean  0.4351  0.4137  0.6318  0.8629    0.0  0.2935
SD    0.0659  0.1623  0.1205  0.0455    0.0  0.0602

In [18]:
print(tuned_gbr)

GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                          init=None, learning_rate=0.15, loss='ls', max_depth=7,
                          max_features=1.0, max_leaf_nodes=None,
                          min_impurity_decrease=0.02, min_impurity_split=None,
                          min_samples_leaf=5, min_samples_split=5,
                          min_weight_fraction_leaf=0.0, n_estimators=230,
                          n_iter_no_change=None, presort='deprecated',
                          random_state=123, subsample=0.85, tol=0.0001,
                          validation_fraction=0.1, verbose=0, warm_start=False)


# モデルの検証

In [19]:
from pycaret.regression import evaluate_model

evaluate_model(tuned_gbr)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Hyperparameters', 'param…

## deploy

In [20]:
from pycaret.regression import finalize_model

final_gbr = finalize_model(tuned_gbr)
print(final_gbr)

GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                          init=None, learning_rate=0.15, loss='ls', max_depth=7,
                          max_features=1.0, max_leaf_nodes=None,
                          min_impurity_decrease=0.02, min_impurity_split=None,
                          min_samples_leaf=5, min_samples_split=5,
                          min_weight_fraction_leaf=0.0, n_estimators=230,
                          n_iter_no_change=None, presort='deprecated',
                          random_state=123, subsample=0.85, tol=0.0001,
                          validation_fraction=0.1, verbose=0, warm_start=False)


In [21]:
from pycaret.regression import predict_model

predict_model(final_gbr);

Model     MAE     MSE    RMSE      R2   RMSLE    MAPE
0  Gradient Boosting Regressor  0.0404  0.0034  0.0585  0.9986  0.0288  0.0305

In [22]:
from pycaret.regression import save_model

save_model(final_gbr, "gbr_model")

Transformation Pipeline and Model Succesfully Saved


(Pipeline(memory=None,
          steps=[('dtypes',
                  DataTypes_Auto_infer(categorical_features=[],
                                       display_types=True, features_todrop=[],
                                       id_columns=[], ml_usecase='regression',
                                       numerical_features=[], target='Score',
                                       time_features=[])),
                 ('imputer',
                  Simple_Imputer(categorical_strategy='not_available',
                                 fill_value_categorical=None,
                                 fill_value_numerical=None,
                                 numeric_strategy='...
                                            learning_rate=0.15, loss='ls',
                                            max_depth=7, max_features=1.0,
                                            max_leaf_nodes=None,
                                            min_impurity_decrease=0.02,
                          

In [23]:
from pycaret.regression import load_model

loaded_gbr = load_model("gbr_model")

Transformation Pipeline and Model Successfully Loaded


# 予測用データの取得

In [24]:
def scrapePredData(homeTeam,awayTeam,TeamNameDic,year):
    team = TeamNameDic[homeTeam]
    team2 = TeamNameDic[awayTeam]
    url = 'https://www.football-lab.jp/' +  team + '/match/' + '?year=' + year
    url2 = 'https://www.football-lab.jp/' +  team2 + '/match/' + '?year=' + year
    #試合結果を取得
    #表を取得
    df = pd.read_html(url)[0]
    df2 = pd.read_html(url2)[0]
    #最後の列を削除
    last_index = df.index[-1]
    last_index2 = df2.index[-1]
    df = df.drop(last_index).drop(df.columns[[2,6,7,8,19,20]], axis=1)
    df2 = df2.drop(last_index2).drop(df2.columns[[2,6,7,8,19,20]], axis=1)
    #homeTeam名追加
    df.insert(2,'Team',homeTeam)
    df2.insert(2,'Team',awayTeam)
    #列名を英語に
    df = df.rename(columns={'相手': 'awayTeam','Unnamed: 5':'H or A','チャンス構築率':'CBP_x','シュート':'shot_x','シュート成功率':'shot acc_x','支配率':'possession_x','攻撃CBP':'ACBP_x','パスCBP':'PassCBP_x','奪取P':'InterceptP_x','守備P':'DP_x'})
    df2 = df2.rename(columns={'相手': 'awayTeam','Unnamed: 5':'H or A','チャンス構築率':'CBP_y','シュート':'shot_y','シュート成功率':'shot acc_y','支配率':'possession_y','攻撃CBP':'ACBP_y','パスCBP':'PassCBP_y','奪取P':'InterceptP_y','守備P':'DP_y'})
    
    #%を変換
    df['CBP_x'] = df['CBP_x'].str.replace('%', '').astype(np.float64) /100
    df['shot acc_x'] = df['shot acc_x'].str.replace('%', '').astype(np.float64) / 100
    df['possession_x'] = df['possession_x'].str.replace('%', '').astype(np.float64) / 100
    df2['CBP_y'] = df2['CBP_y'].str.replace('%', '').astype(np.float64) /100
    df2['shot acc_y'] = df2['shot acc_y'].str.replace('%', '').astype(np.float64) / 100
    df2['possession_y'] = df2['possession_y'].str.replace('%', '').astype(np.float64) / 100

    #一旦書き出して数値化して、平均をとる
    df.to_csv("df.csv",encoding = 'utf-8-sig')
    data = pd.read_csv('/content/df.csv')
    data = data.drop(data.columns[[0]], axis=1)
    data.loc[0] =data.mean()
    df2.to_csv("df2.csv",encoding = 'utf-8-sig')
    data2 = pd.read_csv('/content/df2.csv')
    data2 = data2.drop(data2.columns[[0]], axis=1)
    data2.loc[0] =data2.mean()

    pred = pd.DataFrame(data[:1])
    pred = pred.drop(data.columns[[0,1,4,5]], axis=1)
    pred['Team'] = homeTeam
    pred['awayTeam'] = awayTeam
    pred = pred.rename(columns={'AGI': 'AGI_x','KAGI': 'KAGI_x'})

    pred2 = pd.DataFrame(data2[:1])
    pred2 = pred2.drop(data2.columns[[0,1,2,3,4,5]], axis=1)
    pred2 = pred2.rename(columns={'AGI': 'AGI_y','KAGI': 'KAGI_y'})
    pred = pd.concat([pred, pred2], axis=1)
    return pred


### Team Dic

In [25]:
TeamDic = {'札幌':'276', '仙台':'238', '鹿島':'120', '浦和':'122', '柏':'132', 'FC東京':'270', '川崎Ｆ':'86', '横浜FM':'124', '横浜FC':'296' , '湘南':'130', '清水':'126', '名古屋':'127', 'Ｇ大阪':'128','Ｃ大阪':'133', '神戸':'136','広島':'129', '徳島':'30116', '福岡':'135', '鳥栖':'269', '大分':'207'}
J12021TeamDic = {'札幌':'sapp', '仙台':'send', '鹿島':'kasm', '浦和':'uraw', '柏':'kasw', 'FC東京':'fctk', '川崎Ｆ':'ka-f', '横浜FM':'y-fm', '横浜FC':'y-fc' , '湘南':'shon', '清水':'shim', '名古屋':'nago', 'Ｇ大阪':'g-os','Ｃ大阪':'c-os', '神戸':'kobe','広島':'hiro', '徳島':'toku', '福岡':'fuku', '鳥栖':'tosu', '大分':'oita'}
J12022TeamDic = {'札幌':'sapp', '鹿島':'kasm', '浦和':'uraw', '柏':'kasw', 'FC東京':'fctk', '川崎Ｆ':'ka-f', '横浜FM':'y-fm' , '湘南':'shon', '清水':'shim', '磐田':'iwat','名古屋':'nago', 'Ｇ大阪':'g-os','Ｃ大阪':'c-os', '京都':'kyot','神戸':'kobe','広島':'hiro', '福岡':'fuku', '鳥栖':'tosu'}
J22022TeamDic = {'岩手':'iwte','仙台':'send','秋田':'aki','山形':'yama','水戸':'mito','栃木':'toch','群馬':'gun','大宮':'omiy','千葉':'chib','東京V':'tk-v','町田':'mcd','横浜FC':'y-fc','甲府':'kofu','新潟':'niig','金沢':'kana','岡山':'okay','山口':'r-ya','徳島':'toku','長崎':'ngsk','熊本':'kuma','大分':'oita','琉球':'ryuk'}
def get_keys_from_value(d, val):
    return [k for k, v in d.items() if v == val]

In [26]:
predData = scrapePredData('川崎Ｆ','FC東京',J12021TeamDic,'2021')
predData

Team awayTeam      AGI_x     KAGI_x     CBP_x     shot_x  shot acc_x  \
0  川崎Ｆ     FC東京  59.342105  54.078947  0.123395  14.763158    0.146316   

   possession_x  ACBP_x  PassCBP_x  ...      AGI_y     KAGI_y     CBP_y  \
0      0.546737   21.14  17.727895  ...  52.605263  47.868421  0.098263   

   shot_y  shot acc_y  possession_y     ACBP_y  PassCBP_y  InterceptP_y  \
0    11.5    0.115763      0.462842  13.446316  10.897632     88.429211   

        DP_y  
0  13.911579  

[1 rows x 22 columns]

# 予想

In [27]:
def prediction(homeTeam,awayTeam,TeamDic,year,model):
    predData = scrapePredData(homeTeam,awayTeam,TeamDic,year)
    prediction = predict_model(model, data=predData)
    print(homeTeam,'vs' ,awayTeam , ':' , prediction['Label'][0])
    return 

### ここのTeamを変えれば予想できる

In [32]:
prediction('川崎Ｆ','FC東京', J12022TeamDic ,'2022' , loaded_gbr)

川崎Ｆ vs FC東京 : 0.9373966588944422


In [29]:
prediction('京都','浦和', J12022TeamDic ,'2021' , loaded_gbr)

京都 vs 浦和 : 0.37868442342123876


In [30]:
prediction('広島','鳥栖', J12022TeamDic ,'2021' , loaded_gbr)

広島 vs 鳥栖 : 0.17973458904267448


In [31]:
prediction('清水','札幌', J12022TeamDic ,'2021' , loaded_gbr)

清水 vs 札幌 : -0.24002890986077352


In [ ]:
prediction('福岡','磐田', J12022TeamDic ,'2021' , loaded_gbr)

福岡 vs 磐田 : -0.29523586716353034


In [ ]:
prediction('横浜FM','Ｃ大阪', J12022TeamDic ,'2021' , loaded_gbr)

横浜FM vs Ｃ大阪 : 0.881853961893402


In [ ]:
prediction('Ｇ大阪','鹿島', J12022TeamDic ,'2021' , loaded_gbr)

Ｇ大阪 vs 鹿島 : -0.3269533278380414


In [ ]:
prediction('名古屋','神戸', J12022TeamDic ,'2021' , loaded_gbr)

名古屋 vs 神戸 : -0.3926207258419101


In [ ]:
prediction('湘南','柏', J12022TeamDic ,'2021' , loaded_gbr)

湘南 vs 柏 : -0.033364975789482165


In [ ]:
prediction('長崎','東京V', J22022TeamDic ,'2021' , loaded_gbr)

長崎 vs 東京V : 0.5620813763095822


In [ ]:
prediction('群馬','山形', J22022TeamDic ,'2021' , loaded_gbr)

群馬 vs 山形 : -0.18873081044279416


In [ ]:
prediction('大分','水戸', J22022TeamDic ,'2021' , loaded_gbr)

大分 vs 水戸 : -0.35244147427270983


In [ ]:
prediction('千葉','岩手', J22022TeamDic ,'2021' , loaded_gbr)

千葉 vs 岩手 : 0.03362511019014442
